In [32]:
from dotenv import load_dotenv, find_dotenv

load_dotenv(find_dotenv())

True

In [3]:
PHOENIX_COLLECTOR_ENDPOINT = 'http://localhost:6006'
PHOENIX_COLLECTOR_ENDPOINT_FULL='http://localhost:6006/v1/traces'

In [4]:
PROJECT_NAME = "gpt-researcher"

In [ ]:
import phoenix as px

from phoenix.trace import SpanEvaluations
from phoenix.trace.dsl import SpanQuery

import nest_asyncio
nest_asyncio.apply()

In [7]:
query = SpanQuery().where(
    "'publisher' in metadata['langgraph_node']",
    
).select(
        response="output.value",
)

final_answers_df = px.Client(endpoint=PHOENIX_COLLECTOR_ENDPOINT).query_spans(query, 
                                        project_name=PROJECT_NAME, 
                                        timeout=None)
final_answers_df

response
context.span_id                                                    
b49892a0e8a24747  # # Исследование личностных черт и профессиона...
d3129d1281f511cc  # # Анализ назначения Ивана Ивановича Кротта р...
6a2b236556dd101f  # # Исследование количества близнецов в стране...

In [8]:
import pandas as pd
import re
import requests
from urllib.parse import urlparse

def extract_links(text):
    url_pattern = r'https?://[^\s<>"\'(){}|\\^`\[\]]+'
    return re.findall(url_pattern, text)

def check_link(url):
    try:
        response = requests.get(url, timeout=30)
        if response.status_code == 200:
            domain = urlparse(url).netloc
            if 'example.com' in domain:
                return False
            return True
    except requests.exceptions.RequestException:
        return False
    return False

def calculate_broken_links_percentage(text):
    links = extract_links(text)
    if not links:
        return 0.0
    broken_links = sum(1 for link in links if not check_link(link))
    return (broken_links / len(links)) * 100

final_answers_df['score'] = final_answers_df['response'].apply(calculate_broken_links_percentage)

final_answers_df = final_answers_df[['response', 'score']]
final_answers_df

response      score
context.span_id                                                               
b49892a0e8a24747  # # Исследование личностных черт и профессиона...  18.750000
d3129d1281f511cc  # # Анализ назначения Ивана Ивановича Кротта р...   0.000000
6a2b236556dd101f  # # Исследование количества близнецов в стране...  52.941176

In [9]:
px.Client(endpoint=PHOENIX_COLLECTOR_ENDPOINT).log_evaluations(
    SpanEvaluations(eval_name="Broken Links Percentage", dataframe=final_answers_df),
)

In [8]:
from pathlib import Path
from datetime import datetime
from phoenix.experiments import run_experiment
from phoenix.experiments.types import Example

from run_queries import run_query

Overriding of current TracerProvider is not allowed
Attempting to instrument while already instrumented


OpenTelemetry Tracing Details
|  Phoenix Project: gpt-researcher
|  Span Processor: SimpleSpanProcessor
|  Collector Endpoint: http://localhost:6006/v1/traces
|  Transport: HTTP + protobuf
|  Transport Headers: {}
|  
|  Using a default SpanProcessor. `add_span_processor` will overwrite this default.
|  
|  WARNING: It is strongly advised to use a BatchSpanProcessor in production environments.
|  
|  `register` has set this TracerProvider as the global OpenTelemetry default.
|  To disable this behavior, call `register` with `set_global_tracer_provider=False`.



In [11]:
px_client = px.Client(endpoint=PHOENIX_COLLECTOR_ENDPOINT)

In [13]:
DATA_PATH = Path("./data")
INTERIM_DATA_PATH = DATA_PATH / "interim"

overall_experiment_df = pd.read_json(INTERIM_DATA_PATH / "selected_questions.json", lines=True)
overall_experiment_df

question
0   Проведи исследование и мотивируй схожие черты ...
1   Кротт Иван Иванович назначен ректором Омского ...
2   Проведи исследование и дай мне ответ сколько в...
3   Изучи все материалы и сделай предположение о т...
4   Оцени текущую макроэкономическую ситуацию в Ка...
5   Сравни рождаемость в России после Великой Отеч...
6   Сравни рождаемость в СССР в пятидесятые семиде...
7   Андрей Карпатый сказал о Software 2.0. Найди в...
8   Я являюсь владельцем крупнейшего мессенджера в...
9   Дай более точные рекомендации концепции интегр...
10  Я участвую в пленарной сессии дискуссии на тем...
11  Сравни расходы на финансирование науки в Росси...
12  Как правильно проводить интервью с Познером на...
13  Проанализируй подходы которые помогут команде ...
14  Проведи анализ возможностей боевого применения...
15  Поведи исследование российских онлайн образова...
16  Проведи исследование российских онлайн образов...
17  Проведи анализ развития боевых действий в гори...
18  Проанализируй Основные барьеры внедрения искус...
19  Проанализируй существующие направления исследо...
20  Проведи исследование динамики рынка потребител...
21         Сравни в работах Agentic AI с Agents in AI
22  Разработай для меня план проведения выходного ...
23  Разработай для меня план проведения выходного ...
24  ПЛЕНАРНОЕ СЕССИЯ «БЕСЧЕЛОВЕЧНЫЕ ТЕХНОЛОГИИ: ОС...
25  Подготовь аргументированное выступление для ко...
26  КОНФЕРЕНЦИЯ POSITIVE HACK DAYS\nПЛЕНАРНОЕ СЕСС...

**Upload full dataset**

**Upload test dataset**

**Load test dataset by id**

In [14]:
test_dataset = px_client.get_dataset(name="test_experiment_inputs-2025-06-19 16:56:17")

**Setup task**

In [15]:
async def run_agent(example: Example) -> str:
    result = await run_query(example.input.get("question"))
    return result

**Setup evaluator**

In [16]:
from fact_eval.pipeline import run_fact_pipeline

In [17]:
def evaluate_broken_links(output: str) -> float:    
    return calculate_broken_links_percentage(output[0]['report'])

In [18]:
async def evaluate_citation_trustworthiness(output: str) -> float:    
    return await run_fact_pipeline(output[0]['report'])

**Run experiment on test dataset**

In [19]:
experiment = run_experiment(test_dataset,
                            run_agent,
                            evaluators=[evaluate_broken_links, evaluate_citation_trustworthiness],
                            experiment_name="Test Experiment",
                            experiment_description="Evaluating the test experiment")

🧪 Experiment started.
📺 View dataset experiments: http://127.0.0.1:6006/datasets/RGF0YXNldDoyNg==/experiments
🔗 View this experiment: http://127.0.0.1:6006/datasets/RGF0YXNldDoyNg==/compare?experimentId=RXhwZXJpbWVudDo4


Error in choose_agent: JSONDecodeError('Expecting value: line 1 column 1 (char 0)') ⏳ 00:00<? | ?it/s
Error in reading JSON and failed to repair with json_repair: 'str' object has no attribute 'get'
No JSON found in the string. Falling back to Default Agent.
Error! : HTTPSConnectionPool(host='www.interfax-russia.ru', port=443): Max retries exceeded with url: /academia/ru/news/articles/15561/ (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: unable to get local issuer certificate (_ssl.c:1006)')))
Content too short or empty for https://academia.interfax.ru/ru/news/articles/15561/
Content too short or empty for https://omsk.bezformata.com/listnews/universiteta/147746233/
Content too short or empty for https://bk55.ru/news/article/246098/
🤷 No content found for 'Проведи исследование и мотивируй схожие черты и различия личностных черт и профессиональных качеств Шувалова Игоря Ивановича - руководителя ВЭБ и Грефа Германа Оскарвича -

Worker timeout, requeuing
Worker timeout, requeuing
Worker timeout, requeuing


Error parsing dimension value 100%: invalid literal for int() with base 10: '100%'
Error parsing dimension value 100%: invalid literal for int() with base 10: '100%'
Error! : HTTPSConnectionPool(host='www.sbras.info', port=443): Max retries exceeded with url: /public-reception/question/bliznetsy-cherez-pokolenie-eto-mif (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: unable to get local issuer certificate (_ssl.c:1006)')))
Content too short or empty for http://www.sbras.info/public-reception/question/bliznetsy-cherez-pokolenie-eto-mif
Error parsing dimension value 100%: invalid literal for int() with base 10: '100%'
Error parsing dimension value 100%: invalid literal for int() with base 10: '100%'
Error parsing dimension value 100%: invalid literal for int() with base 10: '100%'
Error parsing dimension value 100%: invalid literal for int() with base 10: '100%'
Error parsing dimension value 100%: invalid literal for int() with

Worker timeout, requeuing
Worker timeout, requeuing
Worker timeout, requeuing


...

Attempt 2 failed: Server disconnected without sending a response.
Content too short or empty for https://academic.oup.com/humrep/article/36/Supplement_1/i10/6294136
Content too short or empty for https://academic.oup.com/humrep/article/36/Supplement_1/i10/6294136
Error loading PDF : https://rosstat.gov.ru/storage/mediabank/Godovoi_demograficheskii_byulleten_za_2022_god.pdf HTTPSConnectionPool(host='rosstat.gov.ru', port=443): Max retries exceeded with url: /storage/mediabank/Godovoi_demograficheskii_byulleten_za_2022_god.pdf (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: unable to get local issuer certificate (_ssl.c:1006)')))
Content too short or empty for https://rosstat.gov.ru/storage/mediabank/Godovoi_demograficheskii_byulleten_za_2022_god.pdf
Error loading PDF : https://rosstat.gov.ru/storage/mediabank/Godovoi_demograficheskii_byulleten_za_2022_god.pdf HTTPSConnectionPool(host='rosstat.gov.ru', port=443): Max retries ex

{'citations': [{'fact': 'Исследования показали: количество родившихся близнецов во всем мире достигло исторического максимума (The Guardian, Великобритания)', 'ref_idx': '0', 'url': 'https://inosmi.ru/20210314/249327267.html'}, {'fact': 'Учёные объяснили, в каких семьях появляются близнецы - Российская газета', 'ref_idx': '0', 'url': 'https://rg.ru/2021/05/15/uchenye-obiasnili-v-kakih-semiah-poiavliaiutsia-bliznecy.html'}, {'fact': 'Теория и практика судебной экспертизы Парамонова Г. В., Дубовик Е. С. Особенности исследования внешнего облика близнецов и близких по сроку рождения родственников - Энциклопедия Судебной Экспертизы', 'ref_idx': '0', 'url': 'http://www.proexpertizu.ru/theory_and_practice/871'}, {'fact': '[источник]', 'ref_idx': '0', 'url': 'https://pilotfm.ru/news/4241'}, {'fact': '[источник]', 'ref_idx': '0', 'url': 'https://infourok.ru/bliznecy-shodstva-i-razlichiya-6871155.html'}, {'fact': '[источник]', 'ref_idx': '0', 'url': 'https://nplus1.ru/news/2021/03/18/tween-peaks

Error in choose_agent: JSONDecodeError('Expecting value: line 1 column 1 (char 0)')
Error in reading JSON and failed to repair with json_repair: 'str' object has no attribute 'get'
No JSON found in the string. Falling back to Default Agent.


{'citations': [{'fact': '[Исследование показало: количество родившихся близнецов во всем мире достигло исторического максимума (The Guardian, Великобритания)]', 'ref_idx': '0', 'url': 'https://inosmi.ru/20210314/249327267.html'}, {'fact': '[Учёные объяснили, в каких семьях появляются близнецы - Российская газета]', 'ref_idx': '0', 'url': 'https://rg.ru/2021/05/15/uchenye-obiasnili-v-kakih-semiah-poiavliaiutsia-bliznecy.html'}, {'fact': '[Теория и практика судебной экспертизы Парамонова Г. В., Дубовик Е. С. Особенности исследования внешнего облика близнецов и близких по сроку рождения родственников - Энциклопедия Судебной Экспертизы]', 'ref_idx': '0', 'url': 'http://www.proexpertizu.ru/theory_and_practice/871'}, {'fact': 'Например, африканские народы демонстрируют самую высокую частоту рождения дизиготных близнецов, в то время как азиаты имеют наименьший показатель ([Исследование показало: количество родившихся близнецов во всем мире достигло исторического максимума (The Guardian, Велик

Error in choose_agent: JSONDecodeError('Expecting value: line 1 column 1 (char 0)')
Error in reading JSON and failed to repair with json_repair: 'list' object has no attribute 'get'
Error in choose_agent: JSONDecodeError('Expecting value: line 1 column 1 (char 0)')
Error in reading JSON and failed to repair with json_repair: 'str' object has no attribute 'get'
No JSON found in the string. Falling back to Default Agent.
Content too short or empty for https://omsk.bezformata.com/listnews/s-i-o-rektora-omgu/146841696/
Content too short or empty for https://omsk.bezformata.com/listnews/professorami/147700454/
Content too short or empty for https://omsk.bezformata.com/listnews/universiteta/147746233/
Error! : HTTPSConnectionPool(host='tabiturient.ru', port=443): Read timed out. (read timeout=4)
running experiment evaluations |████████████████████████| 6/6 (100.0%) | ⏳ 1:35:44<00:00 | 957.38s/it
Error! : HTTPSConnectionPool(host='tabiturient.ru', port=443): Read timed out. (read timeout=4)
E

## Search plugin experiment

Простая проверка на то, нашел ли он результаты по запросу

In [51]:
import logging
import os
import uuid

import httpx

DEFAULT_SEARCH_PLUGIN_MODE = "custom"
DEFAULT_SEARCH_PLUGIN_URL = "https://gigachat.dev.app.sberdevices.ru/retrieval"
DEFAULT_SEARCH_PLUGIN_USER_AGENT = "python-requests/2.32.3"

logger = logging.getLogger(__name__)


class SearchPluginNew:
    """
    SearchPlugin Retriever
    """

    def __init__(self, query, query_domains=None):
        """
        Initializes the SearchPlugin Retriever
        Args:
            query (str): The search query
            query_domains (list, optional): List of domains to search in. Defaults to None.
        """
        self.query = query
        self.query_domains = query_domains or None
        self.api_key = self.get_api_key()

    def get_api_key(self):
        """
        Gets the SearchPlugin API key
        Returns:
        """
        if "SEARCH_PLUGIN_KEY" not in os.environ:
            raise Exception(
                "SearchPlugin API key not found. Please set the SEARCH_PLUGIN_KEY environment variable."
            )
        return os.environ["SEARCH_PLUGIN_KEY"]

    def search(self,
               max_results=7,
               filter_pagelen=7,
               filter_sort=3,
               filter_lang="",
               filter_period="",
               filter_limitcontext="",
               filter_site="",
               filter_mime="",
               ):
        logger.info("SearchPlugin: Searching with query {0}...".format(self.query))

        body = {
            "query": self.query,
            "search_mode": os.environ.get(
                "SEARCH_PLUGIN_MODE", DEFAULT_SEARCH_PLUGIN_MODE
            ),
            "additional_data": {
                "text_sources": {
                    "rambler": {
                        "filter_pagelen": filter_pagelen,
                        "filter_sort": filter_sort,
                        "filter_lang": filter_lang,
                        "filter_period": filter_period,
                        "filter_limitcontext": filter_limitcontext,
                        "filter_site": filter_site,
                        "filter_mime": filter_mime,
                    }
                },
                "references_enabled": True,
                "ranker_enabled": False,
                "doc_count": max_results
            }
        }

        headers = {
            "Authorization": f"{self.get_api_key()}",
            "X-User-ID": str(uuid.uuid4()),
            "X-Client-ID": str(uuid.uuid4()),
            "X-Request-ID": str(uuid.uuid4()),
            "X-Session-ID": str(uuid.uuid4()),
            "User-Agent": os.environ.get(
                "SEARCH_PLUGIN_USER_AGENT", DEFAULT_SEARCH_PLUGIN_USER_AGENT
            ),
        }

        search_response = []

        try:
            with httpx.Client(timeout=60) as client:
                response = client.post(
                    os.environ.get("SEARCH_PLUGIN_URL", DEFAULT_SEARCH_PLUGIN_URL),
                    headers=headers,
                    json=body,
                )

                response.raise_for_status()
                result = response.json()
                documents = result.get("payload", {}).get("documents", [])
                sources = result.get("sources", {})

                for doc in documents:
                    ref = str(doc.get("reference_keyword"))
                    source = sources.get(ref, {})
                    search_response.append(
                            {
                                "title": source.get("title", ""),
                                "href": source.get("url", ""),
                                "body": doc.get("text", ""),
                            }
                        )
        except Exception as e:
            logger.error(repr(e))
            search_response = []
        return search_response

In [77]:
import os
import uuid

import logging

import httpx

DEFAULT_SEARCH_PLUGIN_MODE = "serpapi"
DEFAULT_SEARCH_PLUGIN_URL = "https://gigachat.dev.app.sberdevices.ru/retrieval"
DEFAULT_SEARCH_PLUGIN_USER_AGENT = "python-requests/2.32.3"

class SearchPlugin:
    """
    SearchPlugin Retriever
    """

    def __init__(self, query, query_domains=None):
        """
        Initializes the SearchPlugin Retriever
        Args:
            query (str): The search query
            query_domains (list, optional): List of domains to search in. Defaults to None.
        """
        self.query = query
        self.query_domains = query_domains or None
        self.api_key = self.get_api_key()

    def get_api_key(self):
        """
        Gets the SearchPlugin API key
        Returns:
        """
        if "SEARCH_PLUGIN_KEY" not in os.environ:
            raise Exception(
                "SearchPlugin API key not found. Please set the SEARCH_PLUGIN_KEY environment variable."
            )
        return os.environ["SEARCH_PLUGIN_KEY"]

    def search(self, max_results=7):
        print("SearchPlugin: Searching with query {0}...".format(self.query))

        body = {
            "query": self.query,
            "search_mode": os.environ.get(
                "SEARCH_PLUGIN_MODE", DEFAULT_SEARCH_PLUGIN_MODE
            ),
        }

        headers = {
            "Authorization": f"{self.get_api_key()}",
            "X-User-ID": str(uuid.uuid4()),
            "X-Client-ID": str(uuid.uuid4()),
            "X-Request-ID": str(uuid.uuid4()),
            "X-Session-ID": str(uuid.uuid4()),
            "User-Agent": os.environ.get(
                "SEARCH_PLUGIN_USER_AGENT", DEFAULT_SEARCH_PLUGIN_USER_AGENT
            ),
        }

        search_response = []

        try:
            with httpx.Client() as client:
                response = client.post(
                    os.environ.get("SEARCH_PLUGIN_URL", DEFAULT_SEARCH_PLUGIN_URL),
                    headers=headers,
                    json=body,
                )

                if response.raise_for_status():
                    result = response.json()
                    documents = result.get("payload", {}).get("documents", [])
                    sources = result.get("sources", {})

                    for doc in documents:
                        ref = str(doc.get("reference_keyword"))
                        source = sources.get(ref, {})
                        search_response.append(
                            {
                                "title": source.get("title", ""),
                                "href": source.get("url", ""),
                                "body": doc.get("text", ""),
                            }
                        )
        except Exception as e:
            print(repr(e))
            search_response = []
        return search_response

- Выгрузить из phoenix датасет запросов в поиск. Это dataset для эксперимента.
- Написать функцию прогона search plugin по вопросам.
- Написать оценщик - что он находит какие-то результаты - список не пустой


In [78]:
query = SpanQuery().where(
    'name == "SearchAPIRetriever"',
    
).select(
        request="input.value",
)

search_questions_df = px.Client(endpoint=PHOENIX_COLLECTOR_ENDPOINT).query_spans(query, 
                                        project_name=PROJECT_NAME, 
                                        timeout=None)
search_questions_df

request
context.span_id                                                    
ced2b9828e7e0e11  Проведи исследование и мотивируй схожие черты ...
e86863fd74fef6c4      сравнение лидеров финансового сектора РФ 2025
6adc2bc47cc29bce  личностные качества Игорь Шувалов руководитель...
9413036da8d8413e  профессиональные качества Герман Греф руководи...
e324146aadb41b48  карьерный путь Шувалова и Грефа ключевые дости...
...                                                             ...
55580c5330b617a9  Социальные последствия внедрения искусственног...
ffdae94cd872bb1e  Риски искусственного интеллекта и цифровая тра...
20557452279d98a8  цифровая трансформация влияние на социальную с...
95da7e6c25552968   социальный контракт в эру цифровой трансформации
71b0da1fad04f1f9  Профессиональная переподготовка и инвестиции в...

[351 rows x 1 columns]

In [79]:
test_search_questions_df = search_questions_df.head(10)

In [80]:
test_search_dataset = px_client.get_dataset(name="test_experiment_search-inputs-2025-07-25 18:04:38")

In [81]:
search_dataset = px_client.get_dataset(name="experiment_search-inputs-2025-07-25 18:10:12")

In [82]:
retrievers = [SearchPlugin]
print("Retrievers:", retrievers)

Retrievers: [<class '__main__.SearchPlugin'>]


In [83]:
from gpt_researcher.config.config import Config

config = Config()

In [84]:
import asyncio

In [85]:
sub_query = test_search_questions_df.iloc[1]['request']
retriever = retrievers[0](sub_query)

# Perform the search using the current retriever
async def search_test():
    search_results = await asyncio.to_thread(
        retriever.search, max_results=10
    )
    return search_results
    
research_results = asyncio.run(search_test())
# search_results = retriever.search()

SearchPlugin: Searching with query сравнение лидеров финансового сектора РФ 2025...


In [87]:
async def run_agent(example: Example) -> list[dict[str]]:
    retriever = SearchPlugin(example.input.get("request"))
    search_results = await asyncio.to_thread(
        retriever.search, max_results=10
    )
    return search_results

In [ ]:
async def run_agent_new(example: Example) -> list[dict[str]]:
    retriever = SearchPluginNew(example.input.get("request"))
    search_results = await asyncio.to_thread(
        retriever.search, max_results=10
    )
    return search_results

In [88]:
async def evaluate_search_results(output: list) -> float:
    return 0 if len(output) == 0 else 1

In [89]:
experiment = run_experiment(search_dataset,
                            run_agent,
                            evaluators=[evaluate_search_results],
                            experiment_name="Old Search Plugin",
                            experiment_description="Evaluating test search experiment")

ERROR! Session/line number was not unique in database. History logging moved to new session 1192
🧪 Experiment started.
📺 View dataset experiments: http://127.0.0.1:6006/datasets/RGF0YXNldDoyOA==/experiments
🔗 View this experiment: http://127.0.0.1:6006/datasets/RGF0YXNldDoyOA==/compare?experimentId=RXhwZXJpbWVudDoxMw==


running tasks |          | 0/351 (0.0%) | ⏳ 00:00<? | ?it/s

SearchPlugin: Searching with query Проведи исследование и мотивируй схожие черты и различия личностных черт и профессиональных качеств Шувалова Игоря Ивановича - руководителя ВЭБ и Грефа Германа Оскарвича - руководителя Сбера....SearchPlugin: Searching with query сравнение лидеров финансового сектора РФ 2025...

SearchPlugin: Searching with query личностные качества Игорь Шувалов руководитель ВЭБ...
SearchPlugin: Searching with query профессиональные качества Герман Греф руководитель Сбер...
SearchPlugin: Searching with query карьерный путь Шувалова и Грефа ключевые достижения...
SearchPlugin: Searching with query Психологические особенности лидеров крупных российских компаний (Шувалов, Греф)...
SearchPlugin: Searching with query Профессиональные достижения и общественное влияние Шувалова и Грефа...
SearchPlugin: Searching with query Греф Герман Оскарович профессиональные компетенции и лидерство Сбербанк июль 2025...
SearchPlugin: Searching with query Сравнение управленческих подходов 

running experiment evaluations |          | 0/351 (0.0%) | ⏳ 00:00<? | ?it/s


🔗 View this experiment: http://127.0.0.1:6006/datasets/RGF0YXNldDoyOA==/compare?experimentId=RXhwZXJpbWVudDoxMw==

Experiment Summary (07/25/25 06:23 PM +0300)
--------------------------------------------
                 evaluator    n  n_scores  avg_score
0  evaluate_search_results  351       351   0.418803

Tasks Summary (07/25/25 06:23 PM +0300)
---------------------------------------
   n_examples  n_runs  n_errors
0         351     351         0


In [89]:
experiment = run_experiment(search_dataset,
                            run_agent_new,
                            evaluators=[evaluate_search_results],
                            experiment_name="New Search Plugin",
                            experiment_description="Evaluating test search experiment")

ERROR! Session/line number was not unique in database. History logging moved to new session 1192
🧪 Experiment started.
📺 View dataset experiments: http://127.0.0.1:6006/datasets/RGF0YXNldDoyOA==/experiments
🔗 View this experiment: http://127.0.0.1:6006/datasets/RGF0YXNldDoyOA==/compare?experimentId=RXhwZXJpbWVudDoxMw==


running tasks |          | 0/351 (0.0%) | ⏳ 00:00<? | ?it/s

SearchPlugin: Searching with query Проведи исследование и мотивируй схожие черты и различия личностных черт и профессиональных качеств Шувалова Игоря Ивановича - руководителя ВЭБ и Грефа Германа Оскарвича - руководителя Сбера....SearchPlugin: Searching with query сравнение лидеров финансового сектора РФ 2025...

SearchPlugin: Searching with query личностные качества Игорь Шувалов руководитель ВЭБ...
SearchPlugin: Searching with query профессиональные качества Герман Греф руководитель Сбер...
SearchPlugin: Searching with query карьерный путь Шувалова и Грефа ключевые достижения...
SearchPlugin: Searching with query Психологические особенности лидеров крупных российских компаний (Шувалов, Греф)...
SearchPlugin: Searching with query Профессиональные достижения и общественное влияние Шувалова и Грефа...
SearchPlugin: Searching with query Греф Герман Оскарович профессиональные компетенции и лидерство Сбербанк июль 2025...
SearchPlugin: Searching with query Сравнение управленческих подходов 

running experiment evaluations |          | 0/351 (0.0%) | ⏳ 00:00<? | ?it/s


🔗 View this experiment: http://127.0.0.1:6006/datasets/RGF0YXNldDoyOA==/compare?experimentId=RXhwZXJpbWVudDoxMw==

Experiment Summary (07/25/25 06:23 PM +0300)
--------------------------------------------
                 evaluator    n  n_scores  avg_score
0  evaluate_search_results  351       351   0.418803

Tasks Summary (07/25/25 06:23 PM +0300)
---------------------------------------
   n_examples  n_runs  n_errors
0         351     351         0
